In [14]:
import numpy as np
import pandas as pd
import math as m
from statsmodels.tsa.stattools import acf
from statsmodels.graphics.tsaplots import plot_acf
from scipy import *
import scipy.linalg
import torch
from torch import nn, optim
import mpl_toolkits.mplot3d.axes3d as p3
from sklearn.datasets import make_swiss_roll
from sklearn.preprocessing import MinMaxScaler


import scaleogram as scg
import matplotlib.pyplot as plt
import warnings

from visuals import *
from my_lib import *
from SSA_lib import SSA

In [15]:
warnings.simplefilter('ignore')

plt.rcParams['figure.figsize'] = 16, 8
plt.rcParams['font.family'] = 'DejaVu Serif'
plt.rcParams['lines.linewidth'] = 2
plt.rcParams['lines.markersize'] = 8
plt.rcParams['xtick.labelsize'] = 16
plt.rcParams['ytick.labelsize'] = 16
plt.rcParams['legend.fontsize'] = 16
plt.rcParams['axes.titlesize'] = 24
plt.rcParams['axes.labelsize'] = 8

In [88]:
def Sphere_projection(track2,n = 1):
    
    _x = track2[:,0] - track2[:,0].mean()
    _y = track2[:,1] - track2[:,1].mean()
    _z = track2[:,2] - track2[:,2].mean()
    
    track = np.array([_x,_y,_z]).T
    
    
    for i in range(len(track)):
        track[i] = track[i]/((track[i,:]**2).sum())**.5

    t, p = np.mgrid[0:np.pi:100j, 0:2*np.pi:100j]

    x_s = 0.98*np.sin(t)*np.cos(p)
    y_s = 0.98*np.sin(t)*np.sin(p)
    z_s = 0.98*np.cos(t)

    fig_2 = go.Figure()

    fig_2.add_trace(go.Surface(x=x_s,
                               y=y_s,
                               z=z_s,
                               showscale=False,
                               surfacecolor = z_s))

    fig_2.add_trace(go.Scatter3d(x=track[:,0][::n],
                                 y=track[:,1][::n],
                                 z=track[:,2][::n],
                                 #mode='markers',
                                 marker=dict(
                                             size=2,
                                             line=dict(
                                                        width=0.1
                                                      )

                                             ),
                                 name='trajectory'
                                )
                    )
    
    
    """_x = track3[:,0] - track3[:,0].mean()
    _y = track3[:,1] - track3[:,1].mean()
    _z = track3[:,2] - track3[:,2].mean()
    
    track = np.array([_x,_y,_z]).T
    
    fig_2.add_trace(go.Scatter3d(x=track[:,0][::n],
                                 y=track[:,1][::n],
                                 z=track[:,2][::n],
                                 #mode='markers',
                                 marker=dict(
                                             size=2,
                                             line=dict(
                                                        width=0.1
                                                      )

                                             ),
                                 name='trajectory 2'
                                )
                    )
    
    
    for i in range(len(track)):
        track[i] = track[i]/((track[i,:]**2).sum())**.5"""
        
        
        
    fig_2.add_trace(go.Scatter3d(x=[track[0, 0]],
                               y=[track[0, 1]],
                               z=[track[0, 2]],
                               mode='markers',
                               marker_size=10,
                               marker_color='rgba(255, 10, 0, .7)',
                               name='Start point'))

    fig_2.add_trace(go.Scatter3d(x=[track[-1, 0]],
                               y=[track[-1, 1]],
                               z=[track[-1, 2]],
                               mode='markers',
                               marker_size=10,
                               marker_color='rgba(10, 250, 250, .7)',
                               name='End point'))
    
    

    fig_2.layout.template = 'plotly_white'
    fig_2.show()

    return

In [6]:
device = ('cuda' if torch.cuda.is_available() else 'cpu')

In [16]:
dt = 459*20
#data = pd.read_csv('data/long_walk_100_acc.csv', delimiter =';', decimal=',')[3815+6*455:3815+6*455+dt]
data = pd.read_csv('data/long_walk_100_acc.csv', delimiter =';', decimal=',')[7009:7009+dt]
#data = pd.read_csv('data/long_walk_100_acc.csv', delimiter =';', decimal=',')[3785:8000]
#data = pd.read_csv('data/home_lin_10_lac.csv', delimiter =';', decimal=',')[:]
frecuency = len(data)/(data['time'].values[-1]-data['time'].values[0])
assert 480 < frecuency < 520

x_acc = ( (data['X_value'].values)**2 + (data['Y_value'].values)**2 + (data['Z_value'].values)**2)**.5
_m = np.mean(x_acc)
x_acc -= _m
t = (data['time'].values).astype(float).reshape([-1,])
t = np.linspace(0,t[-1]-t[0],len(x_acc))

fig = go.Figure()
fig.add_scatter(y = x_acc, mode='lines', name='Sum squares')
fig.show()

In [17]:
accel_ssa = SSA(x_acc, 500)

In [18]:
x_acc_clear = accel_ssa.reconstruct(slice(0,5))

In [20]:
def HankelMatrix(X, L):
    
    N = X.shape[0]
    return scipy.linalg.hankel(X[ : N - L + 1], X[N - L : N])

In [23]:
track2, basis2 = phase_track(np.array([x_acc_clear]).T, 600, 3)
plot_phase_track(track2)

Explained variation for 3 principal components: [0.40011295 0.3676284  0.11352861]
Cumulative explained variationfor 3 principal components: 0.8812699616005986



In [59]:
X = HankelMatrix(x_acc_clear,600)
x = torch.from_numpy(X).to(device)

In [81]:

class Autoencoder(nn.Module):
    """Makes the main denoising auto

    Parameters
    ----------
    in_shape [int] : input shape
    enc_shape [int] : desired encoded shape
    """

    def __init__(self, in_shape, enc_shape):
        super(Autoencoder, self).__init__()
        
        self.encode = nn.Sequential(
            nn.Linear(in_shape, 512),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(512, 256),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(256, 128),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(128, 64),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(64, enc_shape),
        )
        
        self.decode = nn.Sequential(
            nn.BatchNorm1d(enc_shape),
            nn.Linear(enc_shape, 64),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(64, 128),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(128, 256),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(256, 512),
            nn.ReLU(True),
            nn.Dropout(0.2),
            nn.Linear(512, in_shape)
        )
        
    def forward(self, x):
        x = self.encode(x)
        x = self.decode(x)
        return x
    
encoder = Autoencoder(in_shape=600, enc_shape=3).double().to(device)

error = nn.MSELoss()

optimizer = optim.Adam(encoder.parameters())

def train(model, error, optimizer, n_epochs, x):
    model.train()
    for epoch in range(1, n_epochs + 1):
        optimizer.zero_grad()
        output = model(x)
        loss = error(output, x)
        loss.backward()
        optimizer.step()
        
        if epoch % int(0.1*n_epochs) == 0:
            print(f'epoch {epoch} \t Loss: {loss.item():.4g}')

In [83]:
train(encoder, error, optimizer, 500, x)

epoch 50 	 Loss: 4.825
epoch 100 	 Loss: 4.489
epoch 150 	 Loss: 4.164
epoch 200 	 Loss: 2.532
epoch 250 	 Loss: 1.398
epoch 300 	 Loss: 1.067
epoch 350 	 Loss: 0.9247
epoch 400 	 Loss: 0.8204
epoch 450 	 Loss: 0.7606
epoch 500 	 Loss: 0.6712


In [84]:
with torch.no_grad():
    encoded = encoder.encode(x)
    decoded = encoder.decode(encoded)
    mse = error(decoded, x).item()
    enc = encoded.cpu().detach().numpy()
    dec = decoded.cpu().detach().numpy()

In [85]:
enc

array([[-17.93850938, -77.43320648,  51.77085454],
       [-19.98650706, -61.72620234,  40.68021508],
       [-19.35824243, -56.86245643,  51.67124814],
       ...,
       [ 10.89177545, -18.03033948,   0.53566571],
       [ 13.0504199 , -21.15980972,  -0.50320833],
       [ 14.38909927, -21.72618766,  -1.59454478]])

In [86]:
fig_2 = go.Figure()


fig_2.add_trace(go.Scatter3d(x=enc[:,0][::],
                             y=enc[:,1][::],
                             z=enc[:,2][::],
                             #mode='markers',
                             marker=dict(
                                         size=0.1,
                                         line=dict(
                                                    width=0.01
                                                  )

                                         ),
                             name='trajectory'
                            )
                )


fig_2.layout.template = 'plotly_white'
fig_2.show()

In [89]:
Sphere_projection(enc, n = 1)